# Cleaning PI Info
In order to prevent duplicate information used to train a model, store PI information separately from list of features.

**Eventually store as SQL database**

In [128]:
import pandas as pd
import numpy as np
from IPython.core.interactiveshell import InteractiveShell
InteractiveShell.ast_node_interactivity = "all"

import cleaning_strings as cln
import importlib as imp
imp.reload(cln);

## Local functions 

In [478]:
def add_zero_zip(df, length, col1 = 'org_zipcode', col2 = 'org_country', country = 'united states'):
    
    '''Add leading zero to New England zipcodes.'''
    
    original = []
    actual = []
    for num in df.ix[(df[col1].str.len() == length) & (df[col2].str.contains(country))][col1]:
        original.append(num)
        num = '0' + num
        actual.append(num)
    return original, actual

def replace_nih_info(df, dict_, org_name = 'org_name'):
    
    '''Some NIH centers have updated names.
    Replace the appropriate grants with this information.'''
    
    for k, v in dict_.items():
        df.replace({k:v}, inplace = True)
        df.ix[df[org_name] == v] = df.ix[df[org_name] == v].fillna(method = 'bfill').fillna(method = 'ffill')
    return df

def add_nih_info(df, col, replace_with, org_name = 'org_name', org_country = 'org_country'):
    
    '''Add NIH information.
    NIH investigators are those whose organization is NOT null,
    but whose country is null.'''
    
    df_replace = pd.DataFrame(df.ix[~df[org_name].isnull() & df[org_country].isnull()]\
                              [col].replace(np.nan, replace_with))
    df_merged = pd.merge(df, df_replace, how = 'left', left_index=True, right_index=True, suffixes=('', '_copy'))
    df_merged[col].fillna(df_merged[col + '_copy'], inplace = True)
    return df_merged

## Cleaning PI information
We want a dataframe where each row is a single PI (no duplicates) and associated organization information as a cross-reference to the grants data.

Import relevant columns from csv with raw grant information.

In [479]:
columns = 'fy pi_ids pi_names org_name org_city org_state org_country org_zipcode org_duns'.split()
dtypes = {key: str for key in columns}

In [480]:
pi_info_raw = pd.read_csv('all_grants.csv', compression = 'gzip', usecols = columns, dtype = dtypes)

#Only analyzing grants from 2000 onwards, as prior to that no funding information is available
pi_info_raw = pi_info_raw.ix[pi_info_raw['fy'] >= '2009']
pi_info_raw.tail()

fy      org_city    org_country   org_duns  \
2223287  2016      lawrence  united states   76248616   
2223288  2016         davis  united states   47120084   
2223289  2016      la jolla  united states  804355790   
2223290  2016  coral gables  united states   52780918   
2223291  2016        toledo  united states   51623734   

                                       org_name org_state org_zipcode  \
2223287           university of kansas lawrence        ks   660457568   
2223288       university of california at davis        ca   956186153   
2223289      university of california san diego        ca   920930934   
2223290  university of miami school of medicine        fl   331462926   
2223291                    university of toledo        oh   436063390   

             pi_ids            pi_names  
2223287   9524770;     mcgill, jodi l.;  
2223288   6490459;   clancy, colleen e;  
2223289   1901669;    feng, gen-sheng ;  
2223290  10944221;     sharifai, nima ;  
2223291   9288457;      liu, song-tao ;

In [481]:
pi_info_cleaned = cln.strip_df(pi_info_raw, ' ', ';', ' ', '.')
pi_info_cleaned.tail()

fy      org_city    org_country   org_duns  \
2223287  2016      lawrence  united states   76248616   
2223288  2016         davis  united states   47120084   
2223289  2016      la jolla  united states  804355790   
2223290  2016  coral gables  united states   52780918   
2223291  2016        toledo  united states   51623734   

                                       org_name org_state org_zipcode  \
2223287           university of kansas lawrence        ks   660457568   
2223288       university of california at davis        ca   956186153   
2223289      university of california san diego        ca   920930934   
2223290  university of miami school of medicine        fl   331462926   
2223291                    university of toledo        oh   436063390   

           pi_ids           pi_names  
2223287   9524770     mcgill, jodi l  
2223288   6490459  clancy, colleen e  
2223289   1901669    feng, gen-sheng  
2223290  10944221     sharifai, nima  
2223291   9288457      liu, song-tao

In [482]:
pi_info_cleaned.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 653801 entries, 1569491 to 2223291
Data columns (total 9 columns):
fy             653801 non-null object
org_city       625577 non-null object
org_country    625632 non-null object
org_duns       611923 non-null object
org_name       653128 non-null object
org_state      617661 non-null object
org_zipcode    622758 non-null object
pi_ids         653801 non-null object
pi_names       653801 non-null object
dtypes: object(9)
memory usage: 49.9+ MB


## Splitting PI Info
Some grants have multiple PIs listed on the grant, and the information for the group of PIs is listed only as the contact PI's information. In order to get unique PI information, these PI groups must be separated into individual PIs.

Split pi_info_cleaned into two dataframes, one containing grouped (multiple) PIs and one containing single PIs.

In [483]:
multi_pi_unsplit = pi_info_cleaned.ix[pi_info_cleaned['pi_ids'].str.contains('contact', na = False)]
pi_info = pi_info_cleaned.drop(multi_pi_unsplit.index)

Drop duplicates to obtain unique PIs that were awarded solo grants. Check both PI IDs and organization name to check for PIs that moved to a different institution.

In [484]:
pi_info.shape
pi_unique = pi_info.drop_duplicates(['pi_ids', 'org_duns'])
pi_unique.shape
pi_unique.tail()

(606233, 9)

(158444, 9)

fy   org_city    org_country   org_duns  \
2223248  2016  champaign  united states   41544081   
2223251  2016      davis  united states   47120084   
2223255  2016    seattle  united states  605799469   
2223258  2016      omaha  united states  168559177   
2223273  2016   hartford  united states  807853791   

                                           org_name org_state org_zipcode  \
2223248  university of illinois at urbana-champaign        il   618207473   
2223251           university of california at davis        ca   956186153   
2223255                    university of washington        wa   981959472   
2223258       university of nebraska medical center        ne   681987835   
2223273     connecticut state dept of public health        ct    61061367   

           pi_ids          pi_names  
2223248   2084901    bolton, eric c  
2223251   9856365   juliano, celina  
2223255  11678618   gerner, michael  
2223258   1873357  sanderson, sam d  
2223273  14753985    gonsalves, lou

Split multiple PIs on PI ID.

In [485]:
multi_pi = cln.split_rows(multi_pi_unsplit, 'pi_ids', by = ';')
multi_pi.tail()

fy   org_city    org_country   org_duns  \
2223041  2016    atlanta  united states   66469933   
2223047  2016   new york  united states   41968306   
2223047  2016   new york  united states   41968306   
2223241  2016  baltimore  united states  188435911   
2223241  2016  baltimore  united states  188435911   

                                 org_name org_state org_zipcode  \
2223041                  emory university        ga   303224250   
2223047               new york university        ny   100122300   
2223047               new york university        ny   100122300   
2223241  university of maryland baltimore        md   212011508   
2223241  university of maryland baltimore        md   212011508   

                                              pi_names              pi_ids  
2223041  jovanovic, tanja ; smith, alicia k. (contact)   8800131 (contact)  
2223047    pyle, anna marie; schlick, tamar  (contact)             1885894  
2223047    pyle, anna marie; schlick, tamar  (contact)   2414701 (contact)  
2223241   kao, joseph pao yung; mayer, dirk  (contact)             8080184  
2223241   kao, joseph pao yung; mayer, dirk  (contact)   9340781 (contact)

Create a df where the '(contact)' string has been stripped from pi_ids; this will allow identification of unique PI IDs (otherwise an ID with '(contact)' appended at the end is viewed as a unique string).

In [486]:
multi_stripped = multi_pi.copy()
multi_stripped['pi_ids'] = multi_stripped['pi_ids'].str.strip(' (contact)')
multi_stripped.tail()

fy   org_city    org_country   org_duns  \
2223041  2016    atlanta  united states   66469933   
2223047  2016   new york  united states   41968306   
2223047  2016   new york  united states   41968306   
2223241  2016  baltimore  united states  188435911   
2223241  2016  baltimore  united states  188435911   

                                 org_name org_state org_zipcode  \
2223041                  emory university        ga   303224250   
2223047               new york university        ny   100122300   
2223047               new york university        ny   100122300   
2223241  university of maryland baltimore        md   212011508   
2223241  university of maryland baltimore        md   212011508   

                                              pi_names   pi_ids  
2223041  jovanovic, tanja ; smith, alicia k. (contact)  8800131  
2223047    pyle, anna marie; schlick, tamar  (contact)  1885894  
2223047    pyle, anna marie; schlick, tamar  (contact)  2414701  
2223241   kao, joseph pao yung; mayer, dirk  (contact)  8080184  
2223241   kao, joseph pao yung; mayer, dirk  (contact)  9340781

Create columns in split multi_pi df denoting whether the PI is the contact and whether the PI ID is already present in the df pi_unique (which contains all PIs that are solo authors of a grant). If the PI is already in pi_unique, we do not need to separate their information again.

In [487]:
multi_pi['contact'] = multi_pi['pi_ids'].str.contains('contact', na = False)
in_pi_unique = multi_stripped['pi_ids'].isin(pi_unique['pi_ids'])
multi_pi['unique_pi'] = in_pi_unique
multi_pi.tail()

fy   org_city    org_country   org_duns  \
2223041  2016    atlanta  united states   66469933   
2223047  2016   new york  united states   41968306   
2223047  2016   new york  united states   41968306   
2223241  2016  baltimore  united states  188435911   
2223241  2016  baltimore  united states  188435911   

                                 org_name org_state org_zipcode  \
2223041                  emory university        ga   303224250   
2223047               new york university        ny   100122300   
2223047               new york university        ny   100122300   
2223241  university of maryland baltimore        md   212011508   
2223241  university of maryland baltimore        md   212011508   

                                              pi_names              pi_ids  \
2223041  jovanovic, tanja ; smith, alicia k. (contact)   8800131 (contact)   
2223047    pyle, anna marie; schlick, tamar  (contact)             1885894   
2223047    pyle, anna marie; schlick, tamar  (contact)   2414701 (contact)   
2223241   kao, joseph pao yung; mayer, dirk  (contact)             8080184   
2223241   kao, joseph pao yung; mayer, dirk  (contact)   9340781 (contact)   

        contact unique_pi  
2223041    True      True  
2223047   False      True  
2223047    True      True  
2223241   False      True  
2223241    True      True

One PI is always designated as a contact if there are multiple PIs listed on a grant. If the PI's ID was not in the df pi_unique, but is listed as a contact (that is, unique_pi == False but contact == True), then we can isolate their information and add this information to pi_unique.

In [488]:
unique_contact = multi_pi[(multi_pi['unique_pi'] == False) & (multi_pi['contact'] == True)]
unique_contact = cln.split_rows(unique_contact, 'pi_names', ';')
unique_contact = unique_contact[unique_contact['pi_names'].str.contains('contact')]
unique_contact = cln.strip_series(unique_contact, ['pi_ids', 'pi_names'])

#shape before dropping duplicates
unique_contact.shape
unique_contact = unique_contact.drop_duplicates('pi_ids org_duns'.split())

#shape after dropping duplicates
unique_contact.shape
unique_contact.tail()

(9196, 11)

(4228, 11)

fy     org_city    org_country   org_duns  \
2221202  2016       tucson  united states   79416826   
2221550  2016  minneapolis  united states  555917996   
2221747  2016    rochester  united states    6471700   
2221778  2016    baltimore  united states   78748558   
2222666  2016       boston  united states   73130411   

                               org_name org_state org_zipcode      pi_ids  \
2221202   synactix pharmaceuticals, inc        az   857182014   10738456    
2221550         university of minnesota        mn   554552070    6169950    
2221747           mayo clinic rochester        mn   559050001    9965561    
2221778                  elixirgen, llc        md   212051511   11903165    
2222666  massachusetts general hospital        ma    21142696    1902302    

        contact unique_pi                  pi_names  
2221202    True     False             li, hong-yu    
2221550    True     False   peterson, kevin arthur   
2221747    True     False     pereira, naveen luke   
2221778    True     False          mano, tomokazu    
2222666    True     False         cahill, daniel p

If the PI ID is neither listed in unique_pi nor are they ever listed as a contact, then we cannot identify whether their organization information is actually different from the contact PI's information. These names will therefore not be split (the IDs are already split).

**Note:** When doing analysis from multiple years, PI IDs should be cross-referenced across years in case a PI did have a solo grant in one year but not in others.

In [489]:
not_contact = multi_pi[(multi_pi['unique_pi'] == False) & (multi_pi['contact'] == False)]
not_contact = not_contact.drop_duplicates('pi_ids org_duns'.split())
not_contact.shape
not_contact.tail()

(7949, 11)

fy    org_city    org_country  org_duns  \
2222255  2016      aurora  united states  41096314   
2222255  2016      aurora  united states  41096314   
2222255  2016      aurora  united states  41096314   
2222458  2016  providence  united states   1785542   
2222666  2016      boston  united states  73130411   

                               org_name org_state org_zipcode  \
2222255   university of colorado denver        co   800452571   
2222255   university of colorado denver        co   800452571   
2222255   university of colorado denver        co   800452571   
2222458                brown university        ri    29129002   
2222666  massachusetts general hospital        ma    21142696   

                                                  pi_names    pi_ids contact  \
2222255  d'sa, viren ; deoni, sean cl (contact); hobbin...  12291424   False   
2222255  d'sa, viren ; deoni, sean cl (contact); hobbin...   6667032   False   
2222255  d'sa, viren ; deoni, sean cl (contact); hobbin...   6870571   False   
2222458  chan, philip andrew; mena, leandro antonio; nu...   8556604   False   
2222666  brastianos, priscilla kaliopi; cahill, daniel ...  11213017   False   

        unique_pi  
2222255     False  
2222255     False  
2222255     False  
2222458     False  
2222666     False

Join all dfs containing unique PI ids.

In [490]:
#Reorder columns so joins can be performed correctly

#unique PIs with a solo grant
cols1 = unique_contact.columns.tolist()
cols1 = cols1[-4:-3] + cols1[-1:] + cols1[0:5]
unique_1 = unique_contact[cols1]

#unique PIs that neither have a solor grant nor are listed as a contact
cols2 = not_contact.columns.tolist()
cols2 = cols2[-3:-2] + cols2[0:6]
unique_2 = not_contact[cols2]

#unique PIs that do not have solo grants but have a
unique_multi = unique_1.append(unique_2)
unique_multi = unique_multi.drop_duplicates('pi_ids org_name'.split())
unique_multi.shape

pi_unique.shape
pi_unique = pi_unique.append(unique_multi)

pi_unique = cln.strip_series(pi_unique, ['pi_ids'], strip = ' ')
pi_unique = pi_unique.drop_duplicates('pi_ids org_name'.split())
pi_unique.shape

(10874, 8)

(158444, 9)

(133121, 9)

## Fixing zipcodes
The leading zero of New England zipcodes was dropped in the raw data. Add leading zero to zipcodes from the US that are length 8 or 4.

In [491]:
pi_unique['org_zipcode'].str.len().value_counts()

9.0     84432
5.0     27251
8.0      7662
7.0       669
4.0       531
6.0       185
3.0       108
1.0        53
10.0       11
2.0        10
Name: org_zipcode, dtype: int64

In [492]:
zip_8, zip_9 = add_zero_zip(pi_unique, 8.0)
zip_4, zip_5 = add_zero_zip(pi_unique, 4.0)

In [493]:
pi_unique['org_zipcode'] = pi_unique['org_zipcode'].replace(zip_8, zip_9)
pi_unique['org_zipcode'] = pi_unique['org_zipcode'].replace(zip_4, zip_5)

In [494]:
pi_unique['org_zipcode'].str.len().value_counts()

9.0     92022
5.0     27383
7.0       669
4.0       399
6.0       185
3.0       108
8.0        72
1.0        53
10.0       11
2.0        10
Name: org_zipcode, dtype: int64

## DUNS numbers
The DUNS number should be a 9-digit number that uniquely identifies an organization. However, the DUNS numbers of organizations changed between 2008 to 2009.

In [154]:
pi_unique.ix[(pi_unique['org_name'].str.contains('stanford', na = False)) & ((pi_unique['fy'] == '2008') | (pi_unique['fy'] == '2009'))]

fy  org_city    org_country   org_duns             org_name  \
1482486  2008  stanford  united states  800771545  stanford university   
1482494  2008  stanford  united states  800771545  stanford university   
1482881  2008  stanford  united states  800771545  stanford university   
1482892  2008  stanford  united states  800771545  stanford university   
1482897  2008  stanford  united states  800771545  stanford university   
1483451  2008  stanford  united states  800771545  stanford university   
1483461  2008  stanford  united states  800771545  stanford university   
1483463  2008  stanford  united states  800771545  stanford university   
1483505  2008  stanford  united states  800771545  stanford university   
1483675  2008  stanford  united states  800771545  stanford university   
1483724  2008  stanford  united states  800771545  stanford university   
1483736  2008  stanford  united states  800771545  stanford university   
1483952  2008  stanford  united states  800771545  stanford university   
1484065  2008  stanford  united states  800771545  stanford university   
1484231  2008  stanford  united states  800771545  stanford university   
1484270  2008  stanford  united states  800771545  stanford university   
1484272  2008  stanford  united states  800771545  stanford university   
1484301  2008  stanford  united states  800771545  stanford university   
1484387  2008  stanford  united states  800771545  stanford university   
1484392  2008  stanford  united states  800771545  stanford university   
1484397  2008  stanford  united states  800771545  stanford university   
1484415  2008  stanford  united states  800771545  stanford university   
1484442  2008  stanford  united states  800771545  stanford university   
1484773  2008  stanford  united states  800771545  stanford university   
1484782  2008  stanford  united states  800771545  stanford university   
1484791  2008  stanford  united states  800771545  stanford university   
1484961  2008  stanford  united states  800771545  stanford university   
1485055  2008  stanford  united states  800771545  stanford university   
1485120  2008  stanford  united states  800771545  stanford university   
1485177  2008  stanford  united states  800771545  stanford university   
1485180  2008  stanford  united states  800771545  stanford university   
1485331  2008  stanford  united states  800771545  stanford university   
1485395  2008  stanford  united states  800771545  stanford university   
1485458  2008  stanford  united states  800771545  stanford university   
1485542  2008  stanford  united states  800771545  stanford university   
1485544  2008  stanford  united states  800771545  stanford university   
1485557  2008  stanford  united states  800771545  stanford university   
1489289  2008  stanford  united states  800771545  stanford university   
1489290  2008  stanford  united states  800771545  stanford university   
1489458  2008  stanford  united states  800771545  stanford university   
1489559  2008  stanford  united states  800771545  stanford university   
1489921  2008  stanford  united states  800771545  stanford university   
1489966  2008  stanford  united states  800771545  stanford university   
1490004  2008  stanford  united states  800771545  stanford university   
1490100  2008  stanford  united states  800771545  stanford university   
1490362  2008  stanford  united states  800771545  stanford university   
1490827  2008  stanford  united states  800771545  stanford university   
1491890  2008  stanford  united states  800771545  stanford university   
1492111  2008  stanford  united states  800771545  stanford university   
1492114  2008  stanford  united states  800771545  stanford university   
1492158  2008  stanford  united states  800771545  stanford university   
1492179  2008  stanford  united states  800771545  stanford university   
1492180  2008  stanford  united states  800771545  stanford university   
1492191  2008  

In [156]:
pi_unique.ix[pi_unique['org_duns'] == '009214214']['org_name'].unique()

array(['burnham institute for medical research', 'stanford university'], dtype=object)

The DUNS number is also not unique between 2008 and 2009.

In [159]:
pi_unique.ix[(pi_unique['org_name'].str.contains('burnham', na = False)) & ((pi_unique['fy'] == '2008') | (pi_unique['fy'] == '2009'))]

fy  org_city    org_country   org_duns  \
1482883  2008  la jolla  united states  009214214   
1484399  2008  la jolla  united states  009214214   
1492092  2008  la jolla  united states  009214214   
1498546  2008  la jolla  united states  009214214   
1498549  2008  la jolla  united states  009214214   
1499820  2008  la jolla  united states  009214214   
1499821  2008  la jolla  united states  009214214   
1499822  2008  la jolla  united states  009214214   
1515340  2008  la jolla  united states  009214214   
1517543  2008  la jolla  united states  009214214   
1521063  2008  la jolla  united states  009214214   
1523138  2008  la jolla  united states  009214214   
1526422  2008  la jolla  united states  009214214   
1532379  2008  la jolla  united states  009214214   
1542992  2008  la jolla  united states  009214214   
1544455  2008  la jolla  united states  009214214   
1553648  2008  la jolla  united states  009214214   
1560479  2008  la jolla  united states  009214214   
1560480  2008  la jolla  united states  009214214   
1560483  2008  la jolla  united states  009214214   
1560484  2008  la jolla  united states  009214214   
1562925  2008  la jolla  united states  009214214   
1562926  2008  la jolla  united states  009214214   
1562927  2008  la jolla  united states  009214214   
1562929  2008  la jolla  united states  009214214   
1573114  2009  la jolla  united states  020520466   
1573116  2009  la jolla  united states  020520466   
1573117  2009  la jolla  united states  020520466   
1573119  2009  la jolla  united states  020520466   
1573120  2009  la jolla  united states  020520466   
1574571  2009  la jolla  united states  020520466   
1574751  2009  la jolla  united states  020520466   
1575140  2009  la jolla  united states  020520466   
1575836  2009  la jolla  united states  020520466   
1576761  2009  la jolla  united states  020520466   
1576870  2009  la jolla  united states  020520466   
1577265  2009  la jolla  united states  020520466   
1577267  2009  la jolla  united states  020520466   
1578364  2009  la jolla  united states  020520466   
1578718  2009  la jolla  united states  020520466   
1579692  2009  la jolla  united states  020520466   
1580372  2009  la jolla  united states  020520466   
1580432  2009  la jolla  united states  020520466   
1580739  2009  la jolla  united states  020520466   
1581065  2009  la jolla  united states  020520466   
1582659  2009  la jolla  united states  020520466   
1582732  2009  la jolla  united states  020520466   
1582733  2009  la jolla  united states  020520466   
1584477  2009  la jolla  united states  020520466   
1584733  2009  la jolla  united states  020520466   
1585030  2009  la jolla  united states  020520466   
1594567  2009  la jolla  united states  020520466   
1594998  2009  la jolla  united states  020520466   
1595350  2009  la jolla  united states  020520466   
1599604  2009  la jolla  united states  020520466   
1599717  2009  la jolla  united states  020520466   
1601734  2009  la jolla  united states  020520466   
1601911  2009  la jolla  united states  020520466   
1603379  2009  la jolla  united states  020520466   
1604313  2009  la jolla  united states  020520466   
1604362  2009  la jolla  united states  020520466   
1604482  2009  la jolla  united states  020520466   
1604950  2009  la jolla  united states  020520466   
1606453  2009  la jolla  united states  020520466   
1611310  2009  la jolla  united states  020520466   
1620474  2009  la jolla  united states  020520466   
1620476  2009  la jolla  united states  020520466   
1620477  2009  la jolla  united states  020520466   
1620490  2009  la jolla  united states  020520466   
1620491  2009  la jolla  united states  020520466   
1620492  2009  la jolla  united states  020520466   
1620493  2009  la jolla  united states  020520466   
1621405  2009  la jolla  united states  020520466   
1621406  2009  la jolla  united states  020520466   
1621408  2009  la jolla  united stat

Replace DUNS numbers from 2008 and earlier with current DUNS numbers.

In [162]:
before_2008 = pi_unique.ix[pi_unique['fy'] <= '2008']
before_2008.shape
after_2008 = pi_unique.ix[pi_unique['fy'] > '2008']
after_2008.shape

(126611, 9)

(90854, 9)

In [186]:
from difflib import SequenceMatcher
def similar(str1, str2):
    return SequenceMatcher(None, str1, str2).ratio()
similar('burnham institute for medical research', 'sanford-burnham medical research instit')

0.6233766233766234

In [190]:
names_after_2008 = after_2008['org_name'].dropna().unique()
names_before_2008 = before_2008['org_name'].dropna().unique()
names_after_2008.shape
names_before_2008.shape

(9219,)

(9926,)

In [191]:
similarity = {}
for i in range(len(names_after_2008)):
    str1 = names_after_2008[i]
    for j in range(len(names_before_2008)):
        str2 = names_before_2008[j]
        sim_ratio = similar(str1, str2)
        if sim_ratio >= 0.5:
            similarity[str1] = (str2, sim_ratio)

In [194]:
similarity

{'iq solutions, inc': ('celsense, inc', 0.5333333333333333),
 'university of massachusetts amherst': ('university legal services', 0.5),
 'fox chase cancer center': ('oregon advocacy center', 0.5777777777777777),
 'duke university': ('university legal services', 0.5),
 'centre for chronic disease control': ('advocacy center for persons w/ disabilit',
  0.5135135135135135),
 'investigaciones medicas en salud': ('xcision medical systems, llc', 0.5),
 'mu-jhu care': ('mu-jhu care', 1.0),
 'universidad nacional mayor de san marcos': ('traditional &modern health practioners',
  0.5128205128205128),
 'h. lee moffitt cancer ctr &res inst': ('cancer research uk cambridge res inst',
  0.5),
 'oregon health &science university': ('oregon advocacy center',
  0.509090909090909),
 'university of california at davis': ('university legal services',
  0.5862068965517241),
 'icahn school of medicine at mount sinai': ('faculty of medicine of timone',
  0.5588235294117647),
 'dana-farber cancer inst': ('

Organization names and DUNS change between 2008 and 2009, and the DUNS are not unique between the two epochs. It will be difficult to cross reference each institution across years. For the first pass, we will only analyze grants from 2009 and later.

In [195]:
pi_unique = pi_unique.ix[pi_unique['fy'] > '2008']

### DUNS numbers of different lengths
DUNS numbers should be 9 digits.

In [495]:
pi_unique['org_duns'].str.len().value_counts()

9.0     89283
8.0     27878
7.0      7516
20.0      384
19.0       59
Name: org_duns, dtype: int64

In [496]:
pi_unique.ix[pi_unique['org_duns'].str.len() == 8.0].head()

fy       org_city    org_country  org_duns  \
1571089  2009        atlanta  united states  13597081   
1571494  2009        warwick  united states  79037218   
1571511  2009      wenatchee  united states  03480039   
1590698  2009  mountain view  united states  60274473   
1591160  2009        atlanta  united states  13597081   

                                         org_name org_state org_zipcode  \
1571089     georgia state dept of human resources        ga   303033181   
1571494               chariho tri-town task force        ri       02889   
1571511  chelan-douglas counties together for dfy        wa       98801   
1590698                       ccs associates, inc        ca   940430816   
1591160     georgia state dept of human resources        ga   303033181   

           pi_ids           pi_names  
1571089   9593571      gibson, jevon  
1571494  11519539  augustinho, paula  
1571511  10159604      hunter, renee  
1590698  10200029   sigman, caroline  
1591160  10374552     brown, stewart

In [497]:
pi_unique.ix[pi_unique['org_duns'].str.len() == 7.0].head()

fy         org_city    org_country org_duns  \
1668444  2010   salt lake city  united states  9095365   
1668446  2010          hampton  united states  3135068   
1668452  2010          chicago  united states  5421136   
1668463  2010       pittsburgh  united states  4514360   
1668472  2010  university park  united states  3403953   

                                        org_name org_state org_zipcode  \
1668444                       university of utah        ut   841128930   
1668446                       hampton university        va   236680108   
1668452                    university of chicago        il   606375418   
1668463   university of pittsburgh at pittsburgh        pa   152132303   
1668472  pennsylvania state university-univ park        pa   168027000   

           pi_ids            pi_names  
1668444   8601681       parks, thomas  
1668446   8206462   harvey, william r  
1668452   8596104  hopkins, michael d  
1668463   2434971    levine, arthur s  
1668472  10378392      foley, henry c

It seems like most of the 8 and 7 digit DUNS numbers are missing leading zeros. Assume this is the case and add leading zeros to DUNS numbers.

In [498]:
def add_zero_duns(df, col1 = 'org_duns'):
    #original = []
    actual = []
    series = df[col1].tolist()
    for num in series:
        #original.append(num)
        if type(num) == float:
            pass
        else:
            while len(num) < 9.0:
                num = '0' + num
        actual.append(num)
    df[col1 + '_'] = actual
    return df

pi_unique = add_zero_duns(pi_unique)
del pi_unique['org_duns']
pi_unique = pi_unique.rename(columns = {'org_duns_':'org_duns'})

Re-organize columns.

In [499]:
old_cols = pi_unique.columns.tolist()
new_cols = old_cols[0:1] + old_cols[-3:-1] + old_cols[-1:] + old_cols[3:4] + old_cols[1:2] + old_cols[4:5] + old_cols[5:6] + old_cols[2:3]
pi_unique = pi_unique[new_cols]
pi_unique.head()

fy   pi_ids            pi_names   org_duns  \
1569491  2009                            ,        NaN   
1569492  2009  1859426        park, no-hee  092530369   
1569493  2009  1864471     forrest, john n  077470003   
1569494  2009  1889505  macrina, francis l  105300446   
1569495  2009  1961084  moore, holly marie  167204994   

                                     org_name       org_city org_state  \
1569491                     iq solutions, inc      rockville        md   
1569492  university of california los angeles    los angeles        ca   
1569493    mount desert island biological lab  salsbury cove        me   
1569494      virginia commonwealth university       richmond        va   
1569495  new york state psychiatric institute       new york        ny   

        org_zipcode    org_country  
1569491   208523003  united states  
1569492   900952000  united states  
1569493       04672  united states  
1569494   232980568  united states  
1569495       10032  united states

According to NIH's description, multiple DUNS are separated by a semi-colon. There are only two groups where multiple DUNS are listed, those with 19 characters and those with 20 characters.

In [500]:
pi_unique.ix[pi_unique['org_duns'].str.len() == 20.0].head()

fy    pi_ids                    pi_names              org_duns  \
1846017  2012   9470515  pacholczyk, rafal wojciech  809593387; 966668691   
1846028  2012   6491945                 dong, zheng  809593387; 966668691   
1846522  2012  10353675               loria, analia  809593387; 966668691   
1846817  2012   2091767          mellor, andrew lee  809593387; 966668691   
1847006  2012  10645764             price, roderick  609980727; 962545658   

                                         org_name org_city org_state  \
1846017                georgia regents university  augusta        ga   
1846028                georgia regents university  augusta        ga   
1846522                georgia regents university  augusta        ga   
1846817                georgia regents university  augusta        ga   
1847006  texas tech university health scis center  lubbock        tx   

        org_zipcode    org_country  
1846017   309120004  united states  
1846028   309120004  united states  
1846522   309120004  united states  
1846817   309120004  united states  
1847006   794306271  united states

In [501]:
pi_unique.ix[pi_unique['org_duns'].str.len() == 19.0].head()

fy    pi_ids                     pi_names             org_duns  \
1669155  2010   9437629  risher, william christopher  809593387;966668691   
1669167  2010   9699188     kelly-cobbs, aisha imani  809593387;966668691   
1669753  2010  10123038               rafikova, olga  809593387;966668691   
1671078  2010   8815155                wu, wei-hua e  809593387;966668691   
1671793  2010   6225753              kohan, donald e  809593387;966668691   

                            org_name org_city org_state org_zipcode  \
1669155  georgia  regents university  augusta        ga   309124810   
1669167  georgia  regents university  augusta        ga   309124810   
1669753  georgia  regents university  augusta        ga   309124810   
1671078  georgia  regents university  augusta        ga   309124810   
1671793  georgia  regents university  augusta        ga   309124810   

           org_country  
1669155  united states  
1669167  united states  
1669753  united states  
1671078  united states  
1671793  united states

For organizations where two DUNS are listed, it seems that both DUNS are used to identify the organization. The only difference between a DUNS with 20 characters and 19 characters is a space after the ';'. Add a space to the 19-length DUNS and replace these values in the df.

In [502]:
#Get the DUNS numbers from pi_unique where the length of the DUNS is 19
len19 = pi_unique.ix[pi_unique['org_duns'].str.len() == 19.0]['org_duns'].values.tolist()

#add a space after the semi-colon
len19_new = []
for i in range(len(len19)):
    len19_new.append(len19[i][:10] + ' ' + len19[i][10:])

#replace the original DUNS of 19 characters
pi_unique['org_duns'] = pi_unique['org_duns'].replace(len19, len19_new)

Remove duplicates by pi_id and org_duns, as a PI can move between institutions.

In [503]:
pi_unique.shape
pi_unique = pi_unique.drop_duplicates('pi_ids org_duns'.split())
pi_unique.shape

(133121, 9)

(132772, 9)

## Examining PIs from non-US countries

In [504]:
pd.set_option('max_rows', 1000)
pi_unique.org_country.value_counts()

united states     127870
canada               392
south africa         249
united kingdom       226
australia            108
switzerland          108
uganda                97
kenya                 89
ethiopia              79
india                 68
china                 65
tanzania u rep        63
zambia                60
nigeria               47
israel                44
france                44
brazil                41
germany               39
peru                  37
netherlands           36
mozambique            35
malawi                35
rwanda                33
vietnam               32
argentina             31
thailand              31
zimbabwe              29
cote d'ivoire         29
sweden                28
botswana              26
haiti                 23
denmark               19
fed micronesia        19
italy                 16
bangladesh            16
mali                  16
pakistan              15
ghana                 15
mexico                14
spain                 14


Although most PIs are from the US, there are a significant number not from the US, and some countries are not listed.

In [505]:
null_country = pi_unique.ix[pi_unique['org_country'].isnull()]
null_country['org_name'].value_counts()

#names of organizations where country is not listed
orgs_null_country = null_country['org_name'].unique()

#names of organizations with zipcode beginning with 20892 (NIH organizations)
nih_orgs = pi_unique.ix[pi_unique['org_zipcode'].str.contains('20892', na = False)]['org_name'].unique()

basic sciences                                           447
niaid extramural activities                              203
diabetes, digestive, kidney diseases                     142
child health and human development                       134
environmental health sciences                            121
heart, lung, and blood institute                         110
aging                                                     89
national institute of mental health                       78
clinical center                                           75
neurological disorders and stroke                         75
cancer epidemiology and genetics                          63
national eye institute                                    59
human genome research                                     57
national institute on drug abuse                          50
dental &craniofacial  research                            41
alcohol abuse and alcoholism                              30
arthritis, musculoskelet

The organizations with no country listed and only one entry are generally misspellings and/or have missing information that can be easily filled. Hard code these data manually.

In [506]:
#fill in missing entries for loyola university entry
pi_unique.loc[1947303].fillna({'org_city':'chicago', 'org_country':'united states'}, inplace = True)

#Danmarks Tekniske
pi_unique.loc[1845456].fillna({'org_duns':'311132885', 'org_city':'Kongens Lyngby', 
                                  'org_country':'Denmark'}, inplace = True)

#Defense Analyses, Inc
pi_unique.loc[1779779].fillna(pi_unique.loc[2172282, :], inplace = True)
pi_unique.loc[2172282].fillna(pi_unique.loc[1779779, :], inplace = True)
pi_unique.loc[2172282].replace({'institute for defense ana':'institute for defense analyses, inc'}, inplace = True)

#UCLA
pi_unique.loc[1845599].replace('california univ los angel', 'university of california los angeles', inplace = True)
pi_unique.loc[1845599].fillna(pi_unique.loc[1846510], inplace = True)

#IIT research
pi_unique.loc[1845463].replace('iit resch institute', 'iit research institute', inplace = True)
pi_unique.loc[1845463].fillna(pi_unique.loc[1667658, :], inplace = True)

#UCSF
rows = [1845453, 1860543]
for row in rows:
    pi_unique.loc[row].replace('california univ san franc', 'university of california, san francisco', inplace = True)
    pi_unique.loc[row].fillna(pi_unique.loc[1574842], inplace = True)

#Omnitec
pi_unique.ix[pi_unique['org_name'].str.contains('omnitec solutions', na = False)] = \
pi_unique.ix[pi_unique['org_name'].str.contains('omnitec solutions', na = False)]\
.fillna(method = 'ffill').fillna(method = 'bfill')

In [507]:
pi_unique.ix[pi_unique['org_country'].isnull()]['org_name'].value_counts(dropna = False)

basic sciences                                           447
niaid extramural activities                              203
NaN                                                      158
diabetes, digestive, kidney diseases                     142
child health and human development                       134
environmental health sciences                            121
heart, lung, and blood institute                         110
aging                                                     89
national institute of mental health                       78
neurological disorders and stroke                         75
clinical center                                           75
cancer epidemiology and genetics                          63
national eye institute                                    59
human genome research                                     57
national institute on drug abuse                          50
dental &craniofacial  research                            41
alcohol abuse and alcoho

### Filling missing NIH information

The remaining grants (except for 'children s hospital medic', which seems like an outlier) seem to all be associated with different NIH centers. Most information of these organizations, that is, DUNS number, city, state and zipcode in addition to country, are missing. There are some NIH centers where all this information is available; however, the name of the center is listed differently.

In [508]:
pi_unique.ix[pi_unique['org_zipcode'].str.contains('20892', na = False)]['org_name'].value_counts()

u.s. national inst allergy & infect dis     4
u.s. national inst/child hlth/human dev     4
u.s. national inst diabetes/digst/kidney    3
u.s. national institute of mental health    3
u.s. national inst/neuro/ds/stroke          1
u.s. national inst alcohol ab/alcoholism    1
u.s. national heart lung and blood inst     1
Name: org_name, dtype: int64

In [509]:
nih_info = pi_unique.ix[pi_unique['org_zipcode'].str.contains('20892', na = False)]
nih_info = nih_info.iloc[:, 3:]
nih_info = nih_info.drop_duplicates('org_duns')
nih_info.index = range(7)
nih_info

org_duns                                  org_name  org_city org_state  \
0  623156465  u.s. national institute of mental health  bethesda        md   
1  623972390   u.s. national inst/child hlth/human dev  bethesda        md   
2  959395492  u.s. national inst diabetes/digst/kidney  bethesda        md   
3  085637655   u.s. national inst allergy & infect dis  bethesda        md   
4  112374603   u.s. national heart lung and blood inst  bethesda        md   
5  176819332        u.s. national inst/neuro/ds/stroke  bethesda        md   
6  022051333  u.s. national inst alcohol ab/alcoholism  bethesda        md   

  org_zipcode    org_country  
0       20892  united states  
1   208922425  united states  
2   208920001  united states  
3   208920001  united states  
4   208922486  united states  
5   208920001  united states  
6   208920001  united states

Replace/fill the corresponding NIH centers in the pi_unique dataframe with the information above.

In [510]:
dict_nih_names = {
    'national institute of allergy and infectious diseases':'u.s. national inst allergy & infect dis',
    'child health and human development':'u.s. national inst/child hlth/human dev',
    'diabetes, digestive, kidney diseases':'u.s. national inst diabetes/digst/kidney',
    'national institute of mental health':'u.s. national institute of mental health',
    'neurological disorders and stroke':'u.s. national inst/neuro/ds/stroke',
    'alcohol abuse and alcoholism':'u.s. national inst alcohol ab/alcoholism',
    'heart, lung, and blood institute':'u.s. national heart lung and blood inst'
}

pi_unique = replace_nih_info(pi_unique, dict_nih_names)

### Adding missing NIH information

In [511]:
pi_unique.ix[pi_unique['org_country'].isnull()]['org_name'].value_counts(dropna = False)

basic sciences                                         447
niaid extramural activities                            203
NaN                                                    158
environmental health sciences                          121
aging                                                   89
clinical center                                         75
cancer epidemiology and genetics                        63
national eye institute                                  59
human genome research                                   57
national institute on drug abuse                        50
dental &craniofacial  research                          41
arthritis, musculoskeletal, skin dis                    30
translational science                                   29
national library of medicine                            27
deafness &other communication disorders                 21
biomedical imaging &bioengineering                      20
clinical sciences                                       

No information about NIH city, state, country and zipcode is listed for the remaining NIH centers. Add this information as bethesda, md, united states and 20892, respectively. **Note:** This address may not be exact, as some NIH institutes/centers may be located elsewhere, but this information will represent general NIH information.

First clean NIH center names.

In [548]:
org_name = pi_unique['org_name'].tolist()
for name in org_name:

str

str

str

str

str

...

str

str

str

str

KeyboardInterrupt: 

In [534]:
and_no_space = pi_unique.loc[pi_unique['org_name'].str.contains(' &[^ ]', na = False)]['org_name']
and_space = pi_unique.loc[pi_unique['org_name'].str.contains(' &[^ ]', na = False)]['org_name'].str.replace('&', '& ')

In [545]:
and_no_space

1569514        h. lee moffitt cancer ctr &res inst
1569517          oregon health &science university
1569525          oregon health &science university
1569540       la jolla inst for allergy &immunolgy
1569603    missouri state dept/ health &senior srv
1569605          oregon health &science university
1569663          oregon health &science university
1569670          oregon health &science university
1569696          oregon health &science university
1569866    rosalind franklin univ of medicine &sci
1569909    university of vermont &st agric college
1569954          oregon health &science university
1569969    university of vermont &st agric college
1569999          oregon health &science university
1570002          oregon health &science university
1570109          oregon health &science university
1570291          oregon health &science university
1570432       la jolla inst for allergy &immunolgy
1570845          oregon health &science university
1570926          oregon health 

In [544]:
and_space

1569514        h. lee moffitt cancer ctr & res inst
1569517          oregon health & science university
1569525          oregon health & science university
1569540       la jolla inst for allergy & immunolgy
1569603    missouri state dept/ health & senior srv
1569605          oregon health & science university
1569663          oregon health & science university
1569670          oregon health & science university
1569696          oregon health & science university
1569866    rosalind franklin univ of medicine & sci
1569909    university of vermont & st agric college
1569954          oregon health & science university
1569969    university of vermont & st agric college
1569999          oregon health & science university
1570002          oregon health & science university
1570109          oregon health & science university
1570291          oregon health & science university
1570432       la jolla inst for allergy & immunolgy
1570845          oregon health & science university
1570926     

In [543]:
pi_unique.ix[pi_unique['org_country'].isnull()]['org_name'].value_counts(dropna = False)

basic sciences                                         447
niaid extramural activities                            203
NaN                                                    158
environmental health sciences                          121
aging                                                   89
clinical center                                         75
cancer epidemiology and genetics                        63
national eye institute                                  59
human genome research                                   57
national institute on drug abuse                        50
dental &craniofacial  research                          41
arthritis, musculoskeletal, skin dis                    30
translational science                                   29
national library of medicine                            27
deafness &other communication disorders                 21
biomedical imaging &bioengineering                      20
clinical sciences                                       

In [88]:
pi_unique = add_nih_info(pi_unique, col = 'org_city', replace_with = 'bethesda')
pi_unique = add_nih_info(pi_unique, col = 'org_state', replace_with = 'md')
pi_unique = add_nih_info(pi_unique, col = 'org_zipcode', replace_with = '20892')
pi_unique = add_nih_info(pi_unique, col = 'org_country', replace_with = 'united states')

In [90]:
to_keep = [col for col in pi_unique.columns if '_copy' not in col]
pi_unique = pi_unique[to_keep]
#pi_unique.filter(regex = '_copy')

## Break 

In [211]:
null_country.ix[null_country['org_name'].isnull()].count()

fy             155
pi_ids         155
pi_names       155
org_duns        65
org_name         0
org_city         0
org_state        0
org_zipcode      0
org_country      0
dtype: int64

In [224]:
null_country.ix[null_country['org_duns'].isnull()].count()

fy             780
pi_ids         780
pi_names       780
org_duns         0
org_name       690
org_city         0
org_state        0
org_zipcode      0
org_country      0
dtype: int64

## Final information 

In [91]:
pi_unique.head(20)

pi_ids                                           pi_names  \
0   10799126                            scott, stuart alexander   
1    7017365                                   polster, brian m   
2    1862210                             zucker, robert alpert    
5    1866930                                        so, peter t   
6    9851446  eden, uri tzvi; frank, loren m; ganguli, surya...   
6   12280974  eden, uri tzvi; frank, loren m; ganguli, surya...   
6   10329759  eden, uri tzvi; frank, loren m; ganguli, surya...   
6   12572655  eden, uri tzvi; frank, loren m; ganguli, surya...   
6   11706552  eden, uri tzvi; frank, loren m; ganguli, surya...   
7   11044822                                    gade, terence p   
8    9335858                                          qi, ling    
9   14380202                                    boxer, matthew    
10  10687426                              demner-fushman, dina    
11   9691085                                   lakatta, edward    
12  10940848  lozano, andres m.; lyketsos, constantine g (co...   
13   1874169                                  clarke, gregory n   
14   6796092                                           guo, su    
15   1939854                           loughran, thomas patrick   
16  10271451                             brewer, carmen crowell   
17   8821769                                steinman, michael a   

                                    org_name            org_city org_state  \
0    icahn school of medicine at mount sinai            new york        ny   
1           university of maryland baltimore           baltimore        md   
2                     university of michigan           ann arbor        mi   
5      massachusetts institute of technology           cambridge        ma   
6              cold spring harbor laboratory  cold spring harbor        ny   
6              cold spring harbor laboratory  cold spring harbor        ny   
6              cold spring harbor laboratory  cold spring harbor        ny   
6              cold spring harbor laboratory  cold spring harbor        ny   
6              cold spring harbor laboratory  cold spring harbor        ny   
7                 university of pennsylvania        philadelphia        pa   
8                         cornell university              ithaca        ny   
9                      translational science            bethesda        md   
10              national library of medicine            bethesda        md   
11                                     aging            bethesda        md   
12                  johns hopkins university           baltimore        md   
13      kaiser foundation research institute             oakland        ca   
14   university of california, san francisco       san francisco        ca   
15                    university of virginia     charlottesville        va   
16  deafness & other communication disorders            bethesda        md   
17   university of california, san francisco       san francisco        ca   

      org_country org_zipcode  
0   united states   100296574  
1   united states   212011508  
2   united states   481091276  
5   united states   021421029  
6   united states   117242209  
6   united states   117242209  
6   united states   117242209  
6   united states   117242209  
6   united states   117242209  
7   united states   191046205  
8   united states   148502820  
9   united states       20892  
10  united states       20892  
11  united states       20892  
12  united states   212051832  
13  united states   946123466  
14  united states   941186215  
15  united states   229044195  
16  united states       20892  
17  united states   941186215

In [92]:
pi_unique.to_csv('pi_info.csv', index = False, compression = 'gzip')